In [1]:
import numpy as np
import tensorflow as tf
import json
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Embedding
from CocktailEmbeddingMaker import CocktailEmbeddingMaker
from CocktailEmbeddingMaker import Eval
import wandb
# 데이터 로드
with open('./train_data.json', 'r') as f:
    json_data = json.load(f)
with open('../flavor.json', 'r') as f:
    flavor_data = json.load(f)
test_user_list = []

attributes = ['ABV', 'boozy', 'sweet', 'sour', 'bitter', 'umami', 'salty', 'astringent', 'Perceived_temperature', 'spicy', 'herbal', 'floral', 'fruity', 'nutty', 'creamy', 'smoky']
# user_num = 5
# for i in range(user_num):
#     user = {}
#     user['user_id'] = i
#     preference = {}
#     user['ABV'] = np.random.randint(0,60)
#     for attribute in attributes[2:]:
#         user[attribute] = np.random.randint(0,100)
#     test_user_list.append(user)


# Random user_list 생성 및 저장
def generate_random_user_list(num_users):
    user_list = []
    attributes = ['ABV', 'boozy', 'sweet', 'sour', 'bitter', 'umami', 'salty', 'astringent', 'Perceived_temperature', 'spicy', 'herbal', 'floral', 'fruity', 'nutty', 'creamy', 'smoky']

    for i in range(num_users):
        user = {
            'user_id': i,
            'ABV': np.random.randint(0, 60),
        }
        for attribute in attributes[2:]:
            user[attribute] = np.random.randint(0, 100)
        user_list.append(user)

    with open(f'user_list_v1_{num_users}.json', 'w') as f:
        json.dump(user_list, f)
    return user_list
    print("Random user_list generated and saved.")

test_user_list =generate_random_user_list(5)

class RecipeGenerationModel:
    #RecipeGenerationModel(cocktail_embedding_maker, wandb_flag=True, max_recipe_length=10)
    def __init__(self, cocktail_embedding_maker,wandb_Flag=False, max_recipe_length=10):
        self.cocktail_embedding_maker = cocktail_embedding_maker
        self.ingredient_ids = cocktail_embedding_maker.ingredient_ids
        self.num_ingredients = cocktail_embedding_maker.num_ingredients
        self.max_recipe_length = max_recipe_length
        self.ingredient_embedding_matrix = cocktail_embedding_maker.create_ingredient_embedding_matrix()
        self.sweep_config = None
        self.evaluation_metrics=None
        self.sweep_id = None
        self.wandb = wandb_Flag
        
        self.total_amount = 200
        self.Eval = Eval(json_data,flavor_data,self.total_amount)
        self.attributes = ['ABV', 'boozy', 'sweet', 'sour', 'bitter', 'umami', 'salty', 'astringent', 'Perceived_temperature', 'spicy', 'herbal', 'floral', 'fruity', 'nutty', 'creamy', 'smoky']
        self.evaluation_metrics = ['diversity', 'abv_match', 'taste_match']
        # Best 모델 판정 및 저장
    def save_best_model(self, performance, abv_match, taste_match, threshold_performance, threshold_abv_match, threshold_taste_match,run_id):

        if performance >= threshold_performance and abv_match >= threshold_abv_match and taste_match >= threshold_taste_match:
            self.model.model.save(f'best_model_{run_id}.h5')
            print("Best model saved.")
        else:
            print("Model does not meet the threshold criteria.")

    def build_model(self):
        hidden_units = 128
        optimizer = 'adam'
        if self.wandb:
            hidden_units = wandb.config.get('hidden_units', 128)
            optimizer =  wandb.config.get('optimizer', 'adam')
        
        model = Sequential([
            Embedding(self.num_ingredients, self.ingredient_embedding_matrix.shape[1],
                      weights=[self.ingredient_embedding_matrix], input_length=self.max_recipe_length, trainable=False),
            LSTM(hidden_units, return_sequences=True),
            LSTM(hidden_units),
            Dense(64, activation='gelu'),
            Dense(self.num_ingredients, activation='softmax')
        ])
        
        model.compile(loss='categorical_crossentropy', optimizer=optimizer,metrics=['accuracy'])
        return model

    def train(self, recipes, epochs=50, batch_size=32,learning_rate=0.001):
        ingredient_sequences = []
        next_ingredients = []

        for recipe in recipes:
            sequence = [self.ingredient_ids[self.cocktail_embedding_maker.normalize_string(ingredient)] for ingredient in recipe]
            for i in range(1, len(sequence)):
                ingredient_sequences.append(sequence[:i])
                next_ingredients.append(sequence[i])

        ingredient_sequences = tf.keras.preprocessing.sequence.pad_sequences(ingredient_sequences, maxlen=self.max_recipe_length)
        next_ingredients = tf.keras.utils.to_categorical(next_ingredients, num_classes=self.num_ingredients)
        evaluation_interval = 5
        if self.wandb:
            # wandb 초기화
            wandb.init(project='cocktail_recipe_generation_v2')
            epochs = wandb.config.get('epochs', 50)
            batch_size = wandb.config.get('batch_size', 32)
            learning_rate = wandb.config.get('lr', 0.001)
            optimizer = wandb.config.get('optimizer', 'adam')
            
        self.model = self.build_model()
        for epoch in range(epochs):
            history = self.model.fit(ingredient_sequences, next_ingredients, epochs=1, batch_size=batch_size, verbose=0)
            loss = history.history['loss'][0]
            accuracy = history.history['accuracy'][0]
            if self.wandb:
                # wandb 로깅
                wandb.log({
                    'epoch': epochs,
                    'loss': loss,
                    'accuracy': accuracy,
                })
        # eval을 호출 해서 평가를 수행하고 결과를 evaluation_result에 저장한다. 
        # 저장후 evaluation_metrics에 지정된 평가 지표 합을 계산해서 performance변수에 저장한다. 
        #wandb에 performance와 개별 평가 지표결과를 로깅한다. 
            # 모델 평가
        # print("evaluating model")

        evaluation_results,recipe_profile_list = self.Eval.evaluate_model(self.model, test_user_list)
        
        for recipe_profile in recipe_profile_list:
            for key in self.attributes:
                wandb.log({key: recipe_profile[key]})
            
       
        # 평가 지표 계산
        performance = sum(evaluation_results[metric] for metric in self.evaluation_metrics)
                # Best 모델 판정 및 저장
        threshold_performance = 2.07
        threshold_abv_match = 0.656
        threshold_taste_match = 0.616
        # save_best_model(self, performance, abv_match, taste_match, threshold_performance, threshold_abv_match, threshold_taste_match,run_id):
        self.save_best_model(
                            performance, 
                            evaluation_results['abv_match'], 
                            evaluation_results['taste_match'], 
                            threshold_performance, 
                            threshold_abv_match, 
                            threshold_taste_match,wandb.run.id) 

        if self.wandb:
            # 평가 지표 로깅
            wandb.log({
                'performance': performance, **evaluation_results})
            wandb.finish()
        return loss, accuracy, performance





# # 모델 학습
# recipe_generation_model.train(train_recipes, epochs=50, batch_size=32)
def train_with_sweep():
    # CocktailEmbeddingMaker 인스턴스 생성
    cocktail_embedding_maker = CocktailEmbeddingMaker(json_data, flavor_data)

    # RecipeGenerationModel 인스턴스 생성
    recipe_generation_model = RecipeGenerationModel(cocktail_embedding_maker, True, max_recipe_length=10)

    # 학습 데이터 준비
    train_recipes = [recipe['recipe'].keys() for recipe in json_data['cocktail_info']]

    # 모델 학습
    loss, accuracy, performance = recipe_generation_model.train(train_recipes)


    return loss, accuracy, performance



sweep_configuration = {
    'method': 'random',
    'name': 'sweep',
    'metric': {'goal': 'maximize', 'name': 'performance'},
    'parameters': 
    {
        'batch_size': {'values': [16,32,64,128]},
        'epochs': {'values': [150,200,300,350]},
        'lr': {'max': 0.1, 'min': 0.00001,'distribution': 'log_uniform'},
        'optimizer': {'values': ['adam', 'sgd', 'rmsprop']},
        'hidden_units': {'values': [64, 128, 256, 512]}
     }
}


sweep_id = wandb.sweep(sweep_configuration, project='cocktail_recipe_generation_v2')
wandb.agent(sweep_id, function=train_with_sweep)



Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: WARNING Malformed sweep config detected! This may cause your sweep to behave in unexpected ways.
wandb: WARNING To avoid this, please fix the sweep config schema violations below:
wandb: WARNING   Violation 1. lr uses log_uniform, where min/max specify base-e exponents. Use log_uniform_values to specify limit values.


Create sweep with ID: ybg999s3
Sweep URL: https://wandb.ai/jennyshin_gist_2024/cocktail_recipe_generation_v2/sweeps/ybg999s3


wandb: Agent Starting Run: g01i089n with config:
wandb: 	batch_size: 64
wandb: 	epochs: 300
wandb: 	hidden_units: 128
wandb: 	lr: 1.0806536325118834
wandb: 	optimizer: adam
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: ann4622-sin (jennyshin_gist_2024). Use `wandb login --relogin` to force relogin
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


c:\Users\user\anaconda3\Lib\site-packages\keras\src\layers\core\embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 277ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
[get_taste_info]recipe_taste_weights : {'ABV': 26.599999999999998, 'boozy': 49.0, 'sweet': 44.0, 'sour': 11.0, 'bitter': 10.0, 'umami': 6.0, 'salty': 4.0, 'astringent': 2.0, 'Perceived_temperature': 25.0, 'spicy': 0.0, 'herbal': 7.0, 'floral': 8.0, 'fruity': 43.0, 'nutty': 0.0, 'creamy': 11.0, 'smoky': 3.0}
[get_taste_info]recipe_taste_weights : {'ABV': 26.599999999999998, 'boozy': 49.0, 'sweet': 44.0, 'sour': 11.0, 'bitter': 10.0, 'umami': 6.0, 'salty': 4.0, 'astringent': 2.0, 'Perceived_temperature': 25.0, 'spicy': 0.0, 'herbal': 7.0, 'floral': 8.0, 'fruity': 43.0, 'nutty': 0.0, 'creamy': 11.0, 'smoky': 3.0}
Recipe Taste Profile: {'ABV': 26.599999

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 290ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
[get_taste_info]recipe_taste_weights : {'ABV': 9.960000000000013, 'boozy': 18.50000000000003, 'sweet': 51.500000000000014, 'sour': 4.000000000000005, 'bitter': 12.000000000000007, 'umami': 13.999999999999996, 'salty': 5.999999999999998, 'astringent': 2.5000000000000036, 'Perceived_temperature': 16.00000000000001, 'spicy': 0.0, 'herbal': 2.5000000000000036, 'floral': 2.0000000000000027, 'fruity': 10.000000000000012, 'nutty': 7.0, 'creamy': 36.49999999999999, 'smoky': 18.999999999999996}
[get_taste_info]recipe_taste_weights : {'ABV': 9.960000000000013, 'boozy': 18.50000000000003, 'sweet': 51.500000000000014, 'sour': 4.000000000000005, 'bitter': 12.000

wandb: Agent Starting Run: sd1z0x2v with config:
wandb: 	batch_size: 64
wandb: 	epochs: 350
wandb: 	hidden_units: 64
wandb: 	lr: 1.0760084962773422
wandb: 	optimizer: adam
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 266ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
[get_taste_info]recipe_taste_weights : {'ABV': 11.325000000000015, 'boozy': 20.50000000000003, 'sweet': 72.0, 'sour': 7.0, 'bitter': 1.0000000000000013, 'umami': 1.0000000000000013, 'salty': 1.0000000000000013, 'astringent': 0.0, 'Perceived_temperature': 21.500000000000004, 'spicy': 0.0, 'herbal': 1.0000000000000013, 'floral': 4.000000000000005, 'fruity': 68.49999999999999, 'nutty': 4.000000000000005, 'creamy': 8.00000000000001, 'smoky': 1.0000000000000013}
[get_taste_info]recipe_taste_weights : {'ABV': 11.325000000000015, 'boozy': 20.50000000000003, 'sweet': 72.0, 'sour': 7.0, 'bitter': 1.0000000000000013, 'umami': 1.0000000000000013, 'salty': 1.00

wandb: Agent Starting Run: yqbsrdgf with config:
wandb: 	batch_size: 16
wandb: 	epochs: 300
wandb: 	hidden_units: 256
wandb: 	lr: 1.0965805347524775
wandb: 	optimizer: sgd
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


--- Logging error ---
Traceback (most recent call last):
  File "c:\Users\user\anaconda3\Lib\site-packages\wandb\sdk\lib\sock_client.py", line 255, in _read_packet_bytes
    data = self._sock.recv(self._bufsize)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
ConnectionResetError: [WinError 10054] 현재 연결은 원격 호스트에 의해 강제로 끊겼습니다

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "c:\Users\user\anaconda3\Lib\site-packages\wandb\sdk\interface\router_sock.py", line 27, in _read_message
    resp = self._sock_client.read_server_response(timeout=1)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\user\anaconda3\Lib\site-packages\wandb\sdk\lib\sock_client.py", line 285, in read_server_response
    data = self._read_packet_bytes(timeout=timeout)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\user\anaconda3\Lib\site-packages\wandb\sdk\lib\sock_client.py", line 259, in _read_packet_bytes
    rai

In [ ]:
wandb.restore('best_model.h5', run_path='wandb/run-20210929_062153-1v5z1z1o/files/best_model.h5')

In [1]:
import wandb

api = wandb.Api()
run = api.run("jennyshin_gist_2024/cocktail_recipe_generation/a9k8jlwi")
best_hyperparams = run.config

# Inference 

In [ ]:


# Inference 함수
def inference(model, user_preference):
    generated_recipe = model.generate_recipe(user_preference)
    return generated_recipe